Mar 7, 2025
In this notebook we will run the HQGA feature selection for our manually segregated datasets

In [1]:
print("GJ")

GJ


In [2]:
from qiskit_aer import AerSimulator
from math import pi
import matplotlib.pyplot as plt

from HQGA import problems_m as p
from HQGA import hqga_algorithm
from HQGA import hqga_utils
from HQGA import utils
import pandas as pd
import numpy as np
from sklearn.preprocessing import LabelEncoder, StandardScaler
from qiskit_ibm_runtime import QiskitRuntimeService


# other libraries
from sklearn.datasets import load_iris
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import  accuracy_score
import os

In [3]:
f_path = "dim_under_15/balanced/processed_Dishonest Internet users.csv"

csv = pd.read_csv(f_path)

print(csv)

     CT_range_4  CU_range_1  LT_range_4  sport  untrustworthy
0             3           0           3      3              1
1             0           2           3      3              0
2             1           0           3      3              0
3             2           0           3      3              0
4             3           0           3      3              1
..          ...         ...         ...    ...            ...
316           1           0           1      2              1
317           0           0           0      2              0
318           0           0           0      2              0
319           0           0           0      2              0
320           1           0           1      2              1

[321 rows x 5 columns]


In [4]:
target = csv.columns[-1]
X = csv.drop([target], axis=1)
y = csv[target]

print(X)
print(y)


# Split data into train and test
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=42)
train_df = pd.concat([X_train, y_train], axis=1)
test_df = pd.concat([X_test, y_test], axis=1)

scaler = StandardScaler()
train_x_sc = scaler.fit_transform(X_train)
test_x_sc = scaler.transform(X_test)

model = RandomForestClassifier(n_estimators=100, random_state=42)

model.fit(train_x_sc, y_train)

model

     CT_range_4  CU_range_1  LT_range_4  sport
0             3           0           3      3
1             0           2           3      3
2             1           0           3      3
3             2           0           3      3
4             3           0           3      3
..          ...         ...         ...    ...
316           1           0           1      2
317           0           0           0      2
318           0           0           0      2
319           0           0           0      2
320           1           0           1      2

[321 rows x 4 columns]
0      1
1      0
2      0
3      0
4      1
      ..
316    1
317    0
318    0
319    0
320    1
Name: untrustworthy, Length: 321, dtype: int64


RandomForestClassifier(random_state=42)

In [5]:
y_pred = model.predict(test_x_sc)
score = accuracy_score(y_test, y_pred)
print("accuracy_score: ", score)

accuracy_score:  1.0


In [9]:
def runFeatSel(train_x_sc, y_train, test_x_sc, y_test, real_quantum_hardware = False):

    num_feat = train_x_sc.shape[1]

    global device_features, problem, params, circuit, gBest, chromosome_evolution, bests
    problem = p.FeatureSelection(num_feat, train_x_sc, y_train, test_x_sc, y_test)    
    if real_quantum_hardware:
        service = QiskitRuntimeService(channel="ibm_quantum", token="6b5f26f9f4e717470feffe87d2e605a80bd98ea5b2ffbd825c16d6a99f49a0293f95e529b425d76329cb1a9c5da584c2c0fd9e9926ac9774c6234cb81b861c82")# c1c57019a5ee715b66178367feda161fa8d15bc0b0a8e490516ca1fb4abc251ef94eb9822e6e7bae111a7ed6c591b80c3ea8cbcdbac26d4f431288f7e4cec930")
        
        backend = service.least_busy(simulator=False, operational=True)
        print("backend: ",backend)
        device_features=hqga_utils.device(backend, isReal = True)
    else:
        backend = AerSimulator()
        device_features=hqga_utils.device(backend, isReal = False)

    # k = 30 // num_feat
    k = backend.num_qubits // num_feat
    print("no of individuals in population: ", k)
    max_gen = 10 #5, earlier were 10
    delta = pi/8
    mu = 0.3
    rho = pi/16
    elitism = hqga_utils.ELITISM_Q

    if elitism == hqga_utils.ELITISM_Q or elitism == hqga_utils.ELITISM_D:
        params = hqga_utils.Parameters(k,max_gen,delta,mu, elitism)
    elif elitism == hqga_utils.ELITISM_R:
        params = hqga_utils.ReinforcementParameters(k,max_gen, delta, rho, mu)
    else:
        print("Please, select one elitism procedure among ELITISM_Q, ELITISM_D and ELITISM_R")

    #presentation hyper-parameters
    params.progressBar = True
    params.verbose = True
    params.draw_circuit = True
    # build circuit
    circuit = hqga_utils.setupCircuit(params.pop_size, problem.dim * problem.num_bit_code)
    gBest, chromosome_evolution, bests, time = hqga_algorithm.runQGA(device_features, circuit, params, problem)
    print("gBest.chr: ",gBest.chr)
    best_features = [index for index, char in enumerate(gBest.chr) if char == '1']
    print("best features: ",best_features)
    clf = RandomForestClassifier(random_state=42)
    clf.fit(train_x_sc[:, best_features], y_train)
    y_pred = clf.predict(test_x_sc[:, best_features])

    # Return accuracy as the fitness score
    accuracy = accuracy_score(y_test, y_pred)
    print("accuracy of selected best features: ", accuracy)

    return best_features, accuracy, time



In [7]:
best_features, accuracy, time = runFeatSel(train_x_sc, y_train, test_x_sc, y_test, real_quantum_hardware=False)

no of individuals in population:  7


Generations:   0%|          | 0/6 [00:00<?, ?it/s]

      ┌───┐┌──────────┐ ░ ┌─┐                                                                                 
q1_0: ┤ H ├┤ Ry(-π/8) ├─░─┤M├─────────────────────────────────────────────────────────────────────────────────
      ├───┤├──────────┤ ░ └╥┘┌─┐                                                                              
q1_1: ┤ H ├┤ Ry(-π/8) ├─░──╫─┤M├──────────────────────────────────────────────────────────────────────────────
      ├───┤├──────────┤ ░  ║ └╥┘┌─┐                                                                           
q1_2: ┤ H ├┤ Ry(-π/8) ├─░──╫──╫─┤M├───────────────────────────────────────────────────────────────────────────
      ├───┤├─────────┬┘ ░  ║  ║ └╥┘┌─┐                                                                        
q1_3: ┤ H ├┤ Ry(π/8) ├──░──╫──╫──╫─┤M├────────────────────────────────────────────────────────────────────────
      ├───┤├─────────┴┐ ░  ║  ║  ║ └╥┘┌─┐                                                                     
q

Generations:  17%|█▋        | 1/6 [00:04<00:24,  4.89s/it]

Fitness values: [0.003, 10000000.0, 0.023618556701030965, 0.15563917525773197, 0.15563917525773197, 0.07516494845360822, 0.15563917525773197]
Best fitness 0.003 ; index best  0
      ┌───┐┌──────────┐ ░                      ░              ░ ┌─┐                                                                                 
q1_0: ┤ H ├┤ Ry(-π/8) ├─░───■──────────────────░──────────────░─┤M├─────────────────────────────────────────────────────────────────────────────────
      ├───┤├──────────┤ ░   │                  ░              ░ └╥┘┌─┐                                                                              
q1_1: ┤ H ├┤ Ry(-π/8) ├─░───┼────■─────────────░──────────────░──╫─┤M├──────────────────────────────────────────────────────────────────────────────
      ├───┤├──────────┤ ░   │    │             ░              ░  ║ └╥┘┌─┐                                                                           
q1_2: ┤ H ├┤ Ry(-π/8) ├─░───┼────┼────■────────░──────────────░──╫──╫─┤M├─────

...

selected_features:  [0, 1]
Fitness values: [0.15563917525773197, 0.18756701030927836, 0.003, 0.022618556701030967, 0.18656701030927836, 0.18756701030927836, 10000000.0]
Best fitness 0.003 ; index best  2
      ┌───┐┌──────────┐ ░                 ░ ┌─────────┐  ░ ┌─┐                                                                                 
q1_0: ┤ H ├┤ Ry(-π/8) ├─░─────────────────░─┤ Ry(π/4) ├──░─┤M├─────────────────────────────────────────────────────────────────────────────────
      └───┘└──────────┘ ░      ┌───┐      ░ └─────────┘  ░ └╥┘┌─┐                                                                              
q1_1: ──────────────────░──────┤ X ├──────░──────────────░──╫─┤M├──────────────────────────────────────────────────────────────────────────────
      ┌───┐┌──────────┐ ░      └─┬─┘      ░              ░  ║ └╥┘┌─┐                                                                           
q1_2: ┤ H ├┤ Ry(-π/8) ├─░────────┼────────░──────────────░──╫──╫─┤M├────────

Generations:  83%|████████▎ | 5/6 [00:24<00:04,  4.90s/it]

      ┌───┐┌─────────┐  ░                      ░              ░ ┌─┐                                                                                 
q1_0: ┤ H ├┤ Ry(π/8) ├──░───■──────────────────░──────────────░─┤M├─────────────────────────────────────────────────────────────────────────────────
      ├───┤├─────────┴┐ ░   │                  ░              ░ └╥┘┌─┐                                                                              
q1_1: ┤ H ├┤ Ry(-π/8) ├─░───┼────■─────────────░──────────────░──╫─┤M├──────────────────────────────────────────────────────────────────────────────
      ├───┤├──────────┤ ░   │    │             ░              ░  ║ └╥┘┌─┐                                                                           
q1_2: ┤ H ├┤ Ry(-π/8) ├─░───┼────┼────■────────░──────────────░──╫──╫─┤M├───────────────────────────────────────────────────────────────────────────
      ├───┤├──────────┤ ░   │    │    │        ░              ░  ║  ║ └╥┘┌─┐                              

Generations: 100%|██████████| 6/6 [00:29<00:00,  4.88s/it]

selected_features:  [0, 2]
selected_features:  [0]
Fitness values: [0.04423711340206182, 10000000.0, 0.004, 0.07416494845360821, 0.09478350515463918, 10000000.0, 0.23811340206185572]
Best fitness 0.004 ; index best  2
The best chromosome is:  1011
The best phenotype is:  1011
Its fitness value is:  0.003
The fitness evaluations to obtain the best:  7
The number of fitness evaluations is:  42
gBest.chr:  1011
best features:  [0, 2, 3]
accuracy of selected best features:  1.0


In [11]:
time
# Q[123]

0.01651906967163086

In [12]:
print("Balanced datasets under dimension 15: ====== ")

dir = "manually_segregated-mar_7/nearly_balanced"  #"dim_under_15/balanced"

above_15_datasets = []

bal_data_res = []

for file in os.listdir(dir):
    print("dataset: ",file)
    f_p = os.path.join(dir, file)
    csv = pd.read_csv(f_p)
    
    target = csv.columns[-1]
    X = csv.drop([target], axis=1)
    y = csv[target]
    
    if(len(X.columns) > 15):
        above_15_datasets.append(file)
        continue

    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=42)
    train_df = pd.concat([X_train, y_train], axis=1)
    test_df = pd.concat([X_test, y_test], axis=1)

    scaler = StandardScaler()
    train_x_sc = scaler.fit_transform(X_train)
    test_x_sc = scaler.transform(X_test)

    best_features, accuracy, time = runFeatSel(train_x_sc, y_train, test_x_sc, y_test, real_quantum_hardware=False)

    bal_data_res.append([file, best_features, accuracy, time])

Balanced datasets under dimension 15: ====== 
dataset:  processed_Breast Cancer Wisconsin (Diagnostic).csv
dataset:  processed_Chess (King-Rook vs. King-Pawn).csv
dataset:  processed_Credit Approval.csv
no of individuals in population:  2


Generations:   0%|          | 0/11 [00:00<?, ?it/s]

        ┌───┐┌──────────┐ ░ ┌─┐                                                                                       
 q10_0: ┤ H ├┤ Ry(-π/8) ├─░─┤M├───────────────────────────────────────────────────────────────────────────────────────
        ├───┤├──────────┤ ░ └╥┘┌─┐                                                                                    
 q10_1: ┤ H ├┤ Ry(-π/8) ├─░──╫─┤M├────────────────────────────────────────────────────────────────────────────────────
        ├───┤├─────────┬┘ ░  ║ └╥┘┌─┐                                                                                 
 q10_2: ┤ H ├┤ Ry(π/8) ├──░──╫──╫─┤M├─────────────────────────────────────────────────────────────────────────────────
        ├───┤├─────────┴┐ ░  ║  ║ └╥┘┌─┐                                                                              
 q10_3: ┤ H ├┤ Ry(-π/8) ├─░──╫──╫──╫─┤M├──────────────────────────────────────────────────────────────────────────────
        ├───┤├──────────┤ ░  ║  ║  ║ └╥┘┌─┐     

Generations:   9%|▉         | 1/11 [00:18<03:00, 18.08s/it]

PrimitiveResult([SamplerPubResult(data=DataBin(c9=BitArray(<shape=(), num_shots=1024, num_bits=15>), c10=BitArray(<shape=(), num_shots=1024, num_bits=15>)), metadata={'shots': 1024, 'circuit_metadata': {}})], metadata={'version': 2})
>>The results got:  PrimitiveResult([SamplerPubResult(data=DataBin(c9=BitArray(<shape=(), num_shots=1024, num_bits=15>), c10=BitArray(<shape=(), num_shots=1024, num_bits=15>)), metadata={'shots': 1024, 'circuit_metadata': {}})], metadata={'version': 2})
pub_res:  DataBin(c9=BitArray(<shape=(), num_shots=1024, num_bits=15>), c10=BitArray(<shape=(), num_shots=1024, num_bits=15>))
c_reg:  c9
cnts:  {'110110100110001': 1, '100001101110110': 1, '110011101101000': 1, '110011101100100': 5, '000010111101101': 1, '101001011111100': 1, '101010101100100': 4, '111010100111001': 1, '101111101100001': 1, '100111111110101': 1, '100101001000100': 1, '110011101000100': 2, '110110011111000': 1, '101011101100100': 4, '010001001101101': 1, '100001101101001': 1, '1001110011000

...

selected_features:  [0, 5]
Fitness values: [0.35876923076923073, 0.33953846153846157, 0.28284615384615386, 0.29346153846153844, 0.41546153846153844]
Best fitness 0.28284615384615386 ; index best  2
       ┌───┐┌─────────┐  ░                      ░              ░ ┌─┐                                                                                       
q19_0: ┤ H ├┤ Ry(π/8) ├──░──────────────────────░──────────────░─┤M├───────────────────────────────────────────────────────────────────────────────────────
       ├───┤├─────────┴┐ ░                      ░              ░ └╥┘┌─┐                                                                                    
q19_1: ┤ H ├┤ Ry(-π/8) ├─░──────────────────────░──────────────░──╫─┤M├────────────────────────────────────────────────────────────────────────────────────
       ├───┤├──────────┤ ░                      ░              ░  ║ └╥┘┌─┐                                                                                 
q19_2: ┤ H ├┤ Ry(-π/8)

Generations:  91%|█████████ | 10/11 [02:58<00:18, 18.12s/it]

selected_features:  [0, 5]
Fitness values: [0.35876923076923073, 0.4443076923076923, 0.28284615384615386, 0.29246153846153844, 0.41546153846153844]
Best fitness 0.28284615384615386 ; index best  2
       ┌───┐┌─────────┐  ░                      ░ ┌──────────┐ ░ ┌─┐                                                                                       
q19_0: ┤ H ├┤ Ry(π/8) ├──░──────────────────────░─┤ Ry(-π/4) ├─░─┤M├───────────────────────────────────────────────────────────────────────────────────────
       ├───┤├─────────┴┐ ░                      ░ ├─────────┬┘ ░ └╥┘┌─┐                                                                                    
q19_1: ┤ H ├┤ Ry(-π/8) ├─░──────────────────────░─┤ Ry(π/4) ├──░──╫─┤M├────────────────────────────────────────────────────────────────────────────────────
       ├───┤├──────────┤ ░                      ░ └─────────┘  ░  ║ └╥┘┌─┐                                                                                 
q19_2: ┤ H ├┤ Ry(-π/8) 

Generations: 100%|██████████| 11/11 [03:16<00:00, 17.89s/it]

selected_features:  [0, 1, 2]
selected_features:  [1]
Fitness values: [0.3213076923076923, 0.3876153846153846, 0.28284615384615386, 0.3203076923076923, 0.3952307692307693]
Best fitness 0.28284615384615386 ; index best  2
The best chromosome is:  111001
The best phenotype is:  111001
Its fitness value is:  0.28284615384615386
The fitness evaluations to obtain the best:  15
The number of fitness evaluations is:  55
gBest.chr:  111001
best features:  [0, 1, 2, 5]
accuracy of selected best features:  0.7211538461538461


In [13]:
bal_data_res

[['processed_Credit Approval.csv',
  [2, 5, 6, 8, 9, 10, 14],
  0.8599033816425121,
  0.0420689582824707],
 ['processed_Hayes Roth.csv', [1, 2, 3], 0.8, 0.029506921768188477],
 ['processed_Liver Disorders.csv',
  [0, 1, 2, 5],
  0.7211538461538461,
  0.030120849609375]]

In [14]:
print("Imbalanced datasets under dimension 15: ====== ")

dir = "manually_segregated-mar_7/imbalanced_smotted"

imbal_data_res = []

for file in os.listdir(dir):
    print("dataset: ",file)
    f_p = os.path.join(dir, file)
    csv = pd.read_csv(f_p)
    
    target = csv.columns[-1]
    X = csv.drop([target], axis=1)
    y = csv[target]
    
    if(len(X.columns) > 15):
        above_15_datasets.append(file)
        continue

    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=42)
    train_df = pd.concat([X_train, y_train], axis=1)
    test_df = pd.concat([X_test, y_test], axis=1)

    scaler = StandardScaler()
    train_x_sc = scaler.fit_transform(X_train)
    test_x_sc = scaler.transform(X_test)

    best_features, accuracy, time = runFeatSel(train_x_sc, y_train, test_x_sc, y_test, real_quantum_hardware=False)

    imbal_data_res.append([file, best_features, accuracy, time])

Imbalanced datasets under dimension 15: ====== 
dataset:  processed_Abalone.csv
no of individuals in population:  3


Generations:   0%|          | 0/11 [00:00<?, ?it/s]

       ┌───┐┌──────────┐ ░ ┌─┐                                                                     
q24_0: ┤ H ├┤ Ry(-π/8) ├─░─┤M├─────────────────────────────────────────────────────────────────────
       ├───┤├──────────┤ ░ └╥┘┌─┐                                                                  
q24_1: ┤ H ├┤ Ry(-π/8) ├─░──╫─┤M├──────────────────────────────────────────────────────────────────
       ├───┤├──────────┤ ░  ║ └╥┘┌─┐                                                               
q24_2: ┤ H ├┤ Ry(-π/8) ├─░──╫──╫─┤M├───────────────────────────────────────────────────────────────
       ├───┤├──────────┤ ░  ║  ║ └╥┘┌─┐                                                            
q24_3: ┤ H ├┤ Ry(-π/8) ├─░──╫──╫──╫─┤M├────────────────────────────────────────────────────────────
       ├───┤├─────────┬┘ ░  ║  ║  ║ └╥┘┌─┐                                                         
q24_4: ┤ H ├┤ Ry(π/8) ├──░──╫──╫──╫──╫─┤M├─────────────────────────────────────────────────────────


Generations:   9%|▉         | 1/11 [00:03<00:33,  3.31s/it]

Fitness values: [0.11553697304768484, 0.13607049067035248, 0.12570421561852108]
Best fitness 0.11553697304768484 ; index best  0
       ┌───┐┌──────────┐ ░                                          ░             ░ ┌─┐                                                                     
q24_0: ┤ H ├┤ Ry(-π/8) ├─░───■──────────────────────────────────────░─────────────░─┤M├─────────────────────────────────────────────────────────────────────
       ├───┤├──────────┤ ░   │                                      ░             ░ └╥┘┌─┐                                                                  
q24_1: ┤ H ├┤ Ry(-π/8) ├─░───┼────■─────────────────────────────────░─────────────░──╫─┤M├──────────────────────────────────────────────────────────────────
       ├───┤├──────────┤ ░   │    │                                 ░             ░  ║ └╥┘┌─┐                                                               
q24_2: ┤ H ├┤ Ry(-π/8) ├─░───┼────┼────■────────────────────────────░─────────────░──╫

...

Generations:  91%|█████████ | 10/11 [03:22<00:19, 19.64s/it]

Fitness values: [0.020473607571896642, 0.2335253003276302, 0.21677975973789587, 0.0685260283946123, 0.06998216235893706, 0.020473607571896642]
Best fitness 0.020473607571896642 ; index best  0
       ┌───┐┌──────────┐ ░                           ░              ░ ┌─┐                                                                                       
q83_0: ┤ H ├┤ Ry(-π/8) ├─░───■───────────────────────░──────────────░─┤M├───────────────────────────────────────────────────────────────────────────────────────
       ├───┤├─────────┬┘ ░   │                       ░              ░ └╥┘┌─┐                                                                                    
q83_1: ┤ H ├┤ Ry(π/8) ├──░───┼────■──────────────────░──────────────░──╫─┤M├────────────────────────────────────────────────────────────────────────────────────
       ├───┤├─────────┤  ░   │    │                  ░              ░  ║ └╥┘┌─┐                                                                                 
q8

Generations: 100%|██████████| 11/11 [03:43<00:00, 20.31s/it]

Fitness values: [0.09100400436840195, 0.12749945394976336, 0.24954277393520208, 0.12749945394976336, 0.06998216235893706, 0.020473607571896642]
Best fitness 0.020473607571896642 ; index best  5
The best chromosome is:  11110
The best phenotype is:  11110
Its fitness value is:  0.012736803785948322
The fitness evaluations to obtain the best:  48
The number of fitness evaluations is:  66
gBest.chr:  11110
best features:  [0, 1, 2, 3]


accuracy of selected best features:  0.9912631962140517


In [15]:
bal_data_res

[['processed_Credit Approval.csv',
  [2, 5, 6, 8, 9, 10, 14],
  0.8599033816425121,
  0.0420689582824707],
 ['processed_Hayes Roth.csv', [1, 2, 3], 0.8, 0.029506921768188477],
 ['processed_Liver Disorders.csv',
  [0, 1, 2, 5],
  0.7211538461538461,
  0.030120849609375]]

In [16]:
imbal_data_res

[['processed_Abalone.csv',
  [0, 1, 2, 5, 6, 7],
  0.8904630269523152,
  0.025970458984375],
 ['processed_Blood Transfusion Service.csv',
  [0, 1, 3],
  0.783625730994152,
  0.026285886764526367],
 ['processed_Breast Cancer.csv',
  [1, 3, 4, 6, 7, 8],
  0.8015267175572519,
  0.023059368133544922],
 ['processed_Climate Model Simulation Crashes.csv',
  [0],
  0.8417508417508418,
  0.031945228576660156],
 ['processed_Dishonest Internet users.csv', [0, 3], 1.0, 0.02612614631652832],
 ['processed_Fertility.csv',
  [1, 4, 6],
  0.9811320754716981,
  0.035593509674072266],
 ['processed_Habermans Survival.csv',
  [0, 1, 2],
  0.7925925925925926,
  0.027294397354125977],
 ['processed_HCV.csv', [3, 6, 7, 8, 10, 11], 0.97125, 0.026107311248779297],
 ['processed_Heart Disease.csv',
  [1, 2, 3, 6, 7, 8, 10, 11, 12],
  0.7926829268292683,
  0.026709318161010742],
 ['processed_ILPD (Indian Liver Patient Dataset).csv',
  [1, 2, 3, 4, 7],
  0.764,
  0.03716588020324707],
 ['processed_Parkinsons.csv',
 

In [20]:
bal_data_res + imbal_data_res

[['processed_Credit Approval.csv',
  [2, 5, 6, 8, 9, 10, 14],
  0.8599033816425121,
  0.0420689582824707],
 ['processed_Hayes Roth.csv', [1, 2, 3], 0.8, 0.029506921768188477],
 ['processed_Liver Disorders.csv',
  [0, 1, 2, 5],
  0.7211538461538461,
  0.030120849609375],
 ['processed_Abalone.csv',
  [0, 1, 2, 5, 6, 7],
  0.8904630269523152,
  0.025970458984375],
 ['processed_Blood Transfusion Service.csv',
  [0, 1, 3],
  0.783625730994152,
  0.026285886764526367],
 ['processed_Breast Cancer.csv',
  [1, 3, 4, 6, 7, 8],
  0.8015267175572519,
  0.023059368133544922],
 ['processed_Climate Model Simulation Crashes.csv',
  [0],
  0.8417508417508418,
  0.031945228576660156],
 ['processed_Dishonest Internet users.csv', [0, 3], 1.0, 0.02612614631652832],
 ['processed_Fertility.csv',
  [1, 4, 6],
  0.9811320754716981,
  0.035593509674072266],
 ['processed_Habermans Survival.csv',
  [0, 1, 2],
  0.7925925925925926,
  0.027294397354125977],
 ['processed_HCV.csv', [3, 6, 7, 8, 10, 11], 0.97125, 0.02

In [23]:
res_data = pd.DataFrame(bal_data_res + imbal_data_res)
res_data.columns = ["Dataset", "Best Features", "Accuracy", "Time"]
res_data.to_csv("manually_segregated-mar_7/res_HQGA/SIM_DIM_UNDER_15/res_sim.csv", index=None)

In [24]:
len(bal_data_res + imbal_data_res)

16

In [21]:
above_15_datasets

['processed_Breast Cancer Wisconsin (Diagnostic).csv',
 'processed_Chess (King-Rook vs. King-Pawn).csv',
 'processed_Cylinder Bands.csv',
 'processed_Diabetic Retinopathy Debrecen.csv',
 'processed_Early Stage Diabetes Risk.csv',
 'processed_Estimation of obesity levels based on eating habits and physical condition.csv',
 'processed_Audiology (Standardized).csv',
 'processed_Autism Screening Adult.csv',
 'processed_Cardiotocography.csv',
 'processed_Cervical Cancer.csv',
 'processed_Dermatology.csv',
 'processed_Hepatitis.csv',
 'processed_Hepatocellular Carcinoma.csv',
 'processed_Lymphography.csv',
 'processed_Primary Tumor.csv',
 'processed_Thoracic Surgery.csv',
 'processed_Thyroid Disease.csv']